# Task1_PBT

Index_X = FSR_for_force, FSR_for_coord

Index_y = force, x_coord, y_coord

Data = Splited by Time

## Best metric (RMSE)

107.476 (ASHA scheduler 97.911)

PBT는 학습되는 중간중간에 하이퍼파라미터를 바꿔가며 최적의 모델로 학습시키는 방법이다.

그래서 PBT로 탐색할 땐 optimizer의 학습률을 조금씩 변화시키는 정도는 고려해볼 수 있으나 모델의 구조를 바꾸는 등의 하이퍼파라미터는 옳지 않다.

optimizer에 관한 하이퍼파라미터를 변형하기 위해서는 optimizer도 save, load코드를 fsr_trainable 클래스에 써줘야 할 것이다.

In [1]:
import ray.tune
import ray.air
import ray.air.integrations.wandb
import ray.tune.schedulers.pb2
from fsr_trainable import FSR_Trainable
import ray.tune.search
import ray.tune.search.optuna
ray.tune.schedulers.pb2.PB2
tuner = ray.tune.Tuner(
    trainable=ray.tune.with_resources(
        FSR_Trainable, {'cpu':2},
    ),
    tune_config=ray.tune.TuneConfig(
        num_samples=1000,
        scheduler=ray.tune.schedulers.PopulationBasedTraining(
            time_attr='time_total_s',
            perturbation_interval=5,
            metric='rmse',
            mode='min',
            hyperparam_mutations={
                'model':['fsr_model.LSTM'],
                'model_args':{
                    'hidden_size':[8, 16, 32, 64, 128],
                    'num_layer':ray.tune.randint(1, 9),
                },
                'criterion':['torch.nn.MSELoss'],
                'optimizer':[
                    'torch.optim.Adam',
                    'torch.optim.NAdam',
                    'torch.optim.Adagrad',
                    'torch.optim.RAdam',
                    'torch.optim.SGD',
                ],
                'optimizer_args':{
                    'lr':ray.tune.loguniform(1e-5, 1e-1),
                },
                'imputer':['sklearn.impute.SimpleImputer'],
                'imputer_args':{
                    'strategy':['mean', 'median'],
                },
                'scaler':[ 
                    'sklearn.preprocessing.StandardScaler',
                    'sklearn.preprocessing.MinMaxScaler',
                    'sklearn.preprocessing.RobustScaler',
                ],
                'index_X': [['FSR_for_force', 'FSR_for_coord']],
                'index_y': [['force', 'x_coord', 'y_coord']],
                'data_loader': ['fsr_data.get_index_splited_by_time']
            },
        ),
    ), 
    run_config=ray.air.RunConfig(
        callbacks=[
            # ray.air.integrations.wandb.WandbLoggerCallback(project='FSR-prediction'),
        ],
        checkpoint_config=ray.air.CheckpointConfig(
            num_to_keep=3,
            checkpoint_score_attribute='rmse',
            checkpoint_score_order='min',
            checkpoint_frequency=5,
            checkpoint_at_end=True,
        ),
    ), 
)

In [2]:
results = tuner.fit()

2023-08-07 04:29:06,172	INFO worker.py:1627 -- Started a local Ray instance. View the dashboard at 127.0.0.1:8265 
2023-08-07 04:29:07,534	INFO tune.py:226 -- Initializing Ray automatically. For cluster usage or custom Ray initialization, call `ray.init(...)` before `Tuner(...)`.
 /home/seokj/workspace/.venv/lib/python3.10/site-packages/ray/tune/tune.py:795: UserWarning:Consider boosting PBT performance by enabling `reuse_actors` as well as implementing `reset_config` for Trainable.


2023-08-07 04:29:20,952	INFO pbt.py:646 -- [pbt]: no checkpoint for trial. Skip exploit for Trial FSR_Trainable_82e58_00003
2023-08-07 04:29:21,161	INFO pbt.py:646 -- [pbt]: no checkpoint for trial. Skip exploit for Trial FSR_Trainable_82e58_00002
2023-08-07 04:29:36,131	INFO pbt.py:646 -- [pbt]: no checkpoint for trial. Skip exploit for Trial FSR_Trainable_82e58_00004
2023-08-07 04:29:39,903	INFO pbt.py:646 -- [pbt]: no checkpoint for trial. Skip exploit for Trial FSR_Trainable_82e58_00007
2023-08-07 04:29:55,038	INFO pbt.py:646 -- [pbt]: no checkpoint for trial. Skip exploit for Trial FSR_Trainable_82e58_00010
2023-08-07 04:30:06,312	INFO pbt.py:646 -- [pbt]: no checkpoint for trial. Skip exploit for Trial FSR_Trainable_82e58_00012
2023-08-07 04:30:08,760	INFO pbt.py:646 -- [pbt]: no checkpoint for trial. Skip exploit for Trial FSR_Trainable_82e58_00013
2023-08-07 04:30:20,598	INFO pbt.py:808 -- 

[PopulationBasedTraining] [Exploit] Cloning trial 82e58_00015 (score = -117.673379) int

In [4]:
result = tuner.restore(
    path='/home/seokj/ray_results/FSR_Trainable_2023-08-07_04-29-03',
    trainable=FSR_Trainable
).get_results()
result

2023-08-07 09:34:14,342	INFO experiment_analysis.py:966 -- No trial data passed in during `ExperimentAnalysis` initialization -- you are most likely loading the experiment after it has completed.
Loading trial data from the experiment checkpoint file. This may result in loading some stale information, since checkpointing is periodic.
2023-08-07 09:34:19,752	WARNING experiment_analysis.py:910 -- Failed to read the results for 2 trials:
- /home/seokj/ray_results/FSR_Trainable_2023-08-07_04-29-03/FSR_Trainable_82e58_00376_376_2023-08-07_04-55-36
- /home/seokj/ray_results/FSR_Trainable_2023-08-07_04-29-03/FSR_Trainable_82e58_00406_406_2023-08-07_04-58-02


ResultGrid<[
  Result(
    metrics={'rmse': 129.90476163001648, 'mae': 40.09599873439811, 'mape': 54516147.818796046, 'done': False, 'trial_id': '82e58_00000', 'experiment_tag': '0'},
    path='/home/seokj/ray_results/FSR_Trainable_2023-08-07_04-29-03/FSR_Trainable_82e58_00000_0_2023-08-07_04-29-07',
    checkpoint=Checkpoint(local_path=/home/seokj/ray_results/FSR_Trainable_2023-08-07_04-29-03/FSR_Trainable_82e58_00000_0_2023-08-07_04-29-07/checkpoint_000020)
  ),
  Result(
    metrics={'rmse': 228.26794159926598, 'mae': 67.59703966213728, 'mape': 9438967902676974.0, 'done': False, 'trial_id': '82e58_00001', 'experiment_tag': '1'},
    path='/home/seokj/ray_results/FSR_Trainable_2023-08-07_04-29-03/FSR_Trainable_82e58_00001_1_2023-08-07_04-29-07',
    checkpoint=Checkpoint(local_path=/home/seokj/ray_results/FSR_Trainable_2023-08-07_04-29-03/FSR_Trainable_82e58_00001_1_2023-08-07_04-29-07/checkpoint_000005)
  ),
  Result(
    error='RayTaskError(RuntimeError)',
    metrics={'rmse': 268.

In [16]:
best = float('inf')
for r in result:
    if r.metrics.get('rmse', None):
        best = min(best, r.metrics['rmse'])
best

107.47608891384839